# **_Big Data e Processamento Distribuído_**
## *Tarefa 2 - Exercício 02*
___________________________
### **Luiz Flavio Pereira**
___________________________
</br>

#### Utilizando o dataset shakespeare.txt, faça uma operação de MapReduce para construir um índice invertido contendo como chave uma palavra e como valor uma lista de linhas onde ela foi mencionada.

______________________
## _Configuração do ambiente para execução no Google Colab_

In [1]:
!apt-get update

Ign:1 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1804/x86_64  InRelease
Ign:2 https://developer.download.nvidia.com/compute/machine-learning/repos/ubuntu1804/x86_64  InRelease
Hit:3 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1804/x86_64  Release
Hit:4 https://cloud.r-project.org/bin/linux/ubuntu bionic-cran40/ InRelease
Hit:5 https://developer.download.nvidia.com/compute/machine-learning/repos/ubuntu1804/x86_64  Release
Hit:6 http://security.ubuntu.com/ubuntu bionic-security InRelease
Hit:7 http://ppa.launchpad.net/c2d4u.team/c2d4u4.0+/ubuntu bionic InRelease
Hit:9 http://archive.ubuntu.com/ubuntu bionic InRelease
Hit:10 http://archive.ubuntu.com/ubuntu bionic-updates InRelease
Hit:11 http://ppa.launchpad.net/cran/libgit2/ubuntu bionic InRelease
Hit:12 http://archive.ubuntu.com/ubuntu bionic-backports InRelease
Hit:14 http://ppa.launchpad.net/deadsnakes/ppa/ubuntu bionic InRelease
Hit:15 http://ppa.launchpad.net/graphics-drivers/ppa/ubuntu bionic

In [2]:
!apt-get install openjdk-8-jdk-headless -qq > /dev/null
!wget -q https://archive.apache.org/dist/spark/spark-3.2.0/spark-3.2.0-bin-hadoop3.2.tgz
!tar xf spark-3.2.0-bin-hadoop3.2.tgz
!pip install -q findspark

___________________________
## _Importação das bibliotecas necessárias à execução do programa_

In [3]:
import findspark
findspark.init('spark-3.2.0-bin-hadoop3.2')

import pyspark
import random

sc = pyspark.SparkContext(appName='T2E2')

from pyspark.sql import SparkSession
spark = SparkSession.builder.getOrCreate()

In [4]:
import string

import nltk
nltk.download('punkt')
nltk.download('stopwords')

stopwords = nltk.corpus.stopwords.words('english')
punctuation = string.punctuation

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


_______________
## _Clonagem da pasta com arquivos no GitHub_

In [5]:
!git clone https://github.com/RafaelDaddio/BigDataAulasPUC.git

fatal: destination path 'BigDataAulasPUC' already exists and is not an empty directory.


__________________
#### O programa será executado baseado em duas abordagens. Na primeira assume-se que existe o interesse no número quantitativo de cada linha do arquivo, respeitando-se sua ordem (A primeira linha é a número 1, a segunda a 2 e assim por diante), independentemente do conteúdo existente nelas ou se estão vazias.
</br>

#### Na segunda abordagem assume-se que o indicador da linha é o texto descritivo que inicia a linha, independentemente de sua numeração, ordem ou texto.

__________________
## _Leitura e gravação de novo arquivo contendo a numeração real das linhas do texto_

#### O arquivo original é lido, um loop for percorre cada linha do texto, fazendo-se a substituição da quebra de linha por uma string contendo o número da linha incrementado por contador mais uma quebra de linha. Em seguida é gerado outro arquivo contendo a numeração da linha no final da mesma. Esse será o arquivo utilizado aqui.

In [6]:
with open ('/content/BigDataAulasPUC/Datasets/shakespeare.txt') as arquivo:
    file_test = arquivo.readlines()

lista = []
cont = 1

for replacer in file_test:
    replacer = replacer.replace('\n', ' ' + str(cont) + ' \n')
    
    # Verifica se eh a ultima linha do texto
    if replacer == file_test[-1]:
        string = replacer
        replacer = string.replace(replacer, replacer + ' ' + str(cont))

    lista.append(replacer)
    cont += 1

# Salva o novo arquivo
arquivo = open("shakespeare_mod.txt", "a")
arquivo.writelines(lista)
arquivo.close()

__________________
## _Leitura do arquivo modificado_

In [7]:
shakespeare_file = '/content/shakespeare_mod.txt'

________________
## _Script para geração do indíce inverso do texto_

In [8]:
# String para subtituicao de caracteres nao alfanumericos
punc = '!"#$%&\'()*+,./:;<=>?@[\\]^_`{|}~-'

# Funcao para geracao dos tokens e numeracao das linhas
def tokenizer(line):
    try:
        # Quebra o arquivo por sentencas
        for sentence in line.split('\n'):
            # Quebra o arquivo em tokens
            token_list = sentence.lower().split()
            # Deleta o trecho contendo o nome da obra @ numero
            del token_list[0]
            # Extrai o ultimo token (numero da linha)
            number_line = int(token_list.pop(-1))

            # Exclui tokens nao alfanumericos e faz a higienizacao dos tokens validos
            for token in token_list:
                for ch in punc:
                    token = token.replace(ch, '')
                if token not in stopwords and token not in punctuation:
                    yield (token, number_line)
    except:
        pass
    
shake_test_RDD = sc.textFile(shakespeare_file)
tokens_RDD = shake_test_RDD.flatMap(tokenizer)

# Agrupa os tokens por chave 
grouped_tokens_RDD = tokens_RDD.groupByKey().sortByKey(True).collect()

# Imprime o resultado
for key, values in grouped_tokens_RDD:
    print(key, set(values))

A saída de streaming foi truncada nas últimas 5000 linhas.
obdurate {127939, 168868, 155367, 59080, 173193, 65612, 8443, 7292, 118623}
obedience {1792, 50946, 19332, 157445, 67718, 20231, 131719, 20361, 143371, 117262, 117263, 8082, 87955, 131839, 39957, 64281, 152090, 60571, 169766, 93736, 62380, 132012, 17970, 33970, 91956, 69950, 117311, 40133, 14662, 45768, 102606, 38480, 27993, 41180, 152156, 62303, 62431, 61793, 150242, 1763, 61798, 132455, 70506, 41835, 37743, 113651, 61940, 14966, 94198, 40185, 159742, 53247}
obedient {40704, 9988, 157703, 140808, 146578, 170770, 99860, 165524, 20249, 117152, 145312, 107174, 100529, 62772, 77627, 48829, 8001, 117316, 47430, 84678, 48843, 48844, 114001, 143953, 72534, 115930, 94562, 85100, 138612, 70655}
obeisance {113459}
oberon {160256, 161538, 160259, 160644, 160261, 162695, 160264, 161549, 160398, 161805, 160277, 161180, 162718, 161188, 161062, 161064, 159657, 161837, 161200, 161585, 161840, 161845, 160569, 160571, 161856, 161218, 160323, 16

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




worths {163799, 164718, 24807}
worthy {144384, 31747, 16388, 33797, 134149, 117770, 27148, 29708, 103950, 159758, 32784, 47633, 108560, 117776, 156178, 110614, 110618, 14876, 57374, 115744, 46113, 156193, 107556, 156197, 57382, 103984, 120369, 16947, 13879, 68091, 103993, 21562, 47675, 27196, 76349, 84027, 144447, 163389, 67138, 63560, 25162, 85071, 136784, 141393, 57427, 70741, 14934, 141397, 141398, 85600, 26210, 13412, 17508, 153196, 20593, 48754, 58995, 95857, 122485, 46710, 94327, 73337, 133242, 156793, 85116, 163965, 62593, 55939, 130180, 69253, 67208, 134281, 84106, 144522, 41100, 121484, 121496, 149146, 121499, 21148, 174749, 72354, 61091, 144555, 62134, 27834, 19645, 44733, 85698, 75978, 33998, 18639, 153810, 21203, 125651, 11990, 16090, 13531, 149215, 34016, 141025, 85733, 18662, 90854, 163559, 153835, 128241, 122098, 104182, 124662, 86268, 154369, 151815, 66826, 72461, 14094, 14096, 81682, 84758, 24856, 143130, 91931, 46876, 150811, 19230, 153888, 46884, 108837, 159015, 118

__________________
## _Leitura do arquivo original_

#### Nessa abordagem assume-se que o indicador de posição da linha eh o token no formato **nome_da_obra@numero**, independentemente de sua ordem ou posição

In [9]:
shakespeare_file = '/content/BigDataAulasPUC/Datasets/shakespeare.txt'

________________
## _Script para geração do indíce inverso do texto_

In [10]:
# String para subtituicao de caracteres nao alfanumericos
punc = '!"#$%&\'()*+,./:;<=>?@[\\]^_`{|}~-'

# Funcao para geracao dos tokens e numeracao das linhas
def tokenizer(line):
    try:
        # Quebra o arquivo por sentencas
        for sentence in line.split('\n'):
            # Quebra o arquivo em tokens
            token_list = sentence.lower().split()
            # Extrai o trecho contendo o nome da obra @ numero que sera o indicador da linha
            number_line = token_list.pop(0)

            # Exclui tokens nao alfanumericos e faz a higienizacao dos tokens validos
            for token in token_list:
                for ch in punc:
                    token = token.replace(ch, '')
                if token not in stopwords and token not in punctuation:
                    yield (token, number_line)
    except:
        pass
    
shake_test_RDD = sc.textFile(shakespeare_file)
tokens_RDD = shake_test_RDD.flatMap(tokenizer)

# Agrupa os tokens por chave
grouped_tokens_RDD = tokens_RDD.groupByKey().sortByKey(True).collect()

# Imprime o resultado
for key, values in grouped_tokens_RDD:
    print(key, set(values))

A saída de streaming foi truncada nas últimas 5000 linhas.
bounce {'2kinghenryiv@87594', 'kingjohn@35851'}
bounced {'periclesprinceoftyre@26775', 'various@3753'}
bouncing {'midsummersnightsdream@19818'}
bound {'merchantofvenice@16135', 'asyoulikeit@103085', 'juliuscaesar@105735', '1kinghenryiv@54136', 'kinglear@45775', 'muchadoaboutnothing@94391', 'timonofathens@15141', 'romeoandjuliet@12988', 'loveslabourslost@28804', '2kinghenryvi@82089', 'kingrichardiii@2646', 'romeoandjuliet@23709', '2kinghenryiv@82496', 'tamingoftheshrew@32504', 'kinghenryviii@87173', 'kinglear@7628', 'venusandadonis@37228', 'cymbeline@44667', 'hamlet@32615', '1kinghenryvi@34207', 'glossary@25882', 'winterstale@79027', 'allswellthatendswell@72604', 'loveslabourslost@46804', 'othello@79294', 'titusandronicus@84475', 'othello@76507', 'periclesprinceoftyre@106296', 'kingrichardii@34983', 'comedyoferrors@82830', '1kinghenryiv@57431', 'timonofathens@25835', 'kinghenryviii@91800', 'muchadoaboutnothing@105990', 'glossary

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



A saída de streaming foi truncada nas últimas 5000 linhas.
punched {'kingrichardiii@166002'}
punish {'kingrichardiii@55042', 'periclesprinceoftyre@111458', 'winterstale@6177', '1kinghenryiv@126570', 'hamlet@116010', 'asyoulikeit@16967', 'antonyandcleopatra@131143', '1kinghenryiv@84522', 'antonyandcleopatra@50052', 'periclesprinceoftyre@12291', 'coriolanus@129522', 'kinghenryviii@61898', 'measureforemeasure@106352', 'kinghenryv@31809', 'coriolanus@78523', '2kinghenryiv@19668', 'kinglear@82696', 'twelfthnight@104508', 'measureforemeasure@116052'}
punishd {'winterstale@60515', '3kinghenryvi@110304', 'kinglear@109385', 'kingjohn@42557', 'coriolanus@138565', 'kingjohn@23020', '2kinghenryvi@54109', 'twogentlemenofverona@35480', 'romeoandjuliet@143591', 'hamlet@173747', 'kinghenryv@31673', 'periclesprinceoftyre@12057', 'kinglear@56385', 'cymbeline@64264', 'tempest@70092'}
punished {'kinglear@88291', 'kinghenryv@32347', 'winterstale@111146', 'asyoulikeit@70841', 'romeoandjuliet@144199', 'loves

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



withoutbook {'romeoandjuliet@23209'}
withoutdoor {'winterstale@29142'}
withs {'antonyandcleopatra@67001', 'coriolanus@124749'}
withstand {'2kinghenryvi@118405', '3kinghenryvi@100364'}
withstood {'kingrichardii@9270'}
witht {'twogentlemenofverona@62252', 'winterstale@67183', 'tempest@26211', 'winterstale@45184'}
witless {'troilusandcressida@145540', 'tamingoftheshrew@51561', 'measureforemeasure@13677'}
witness {'measureforemeasure@113857', 'winterstale@95190', 'kingrichardiii@128821', 'twogentlemenofverona@83993', 'muchadoaboutnothing@49199', 'kingrichardiii@21429', 'kinghenryv@153565', 'allswellthatendswell@128684', 'macbeth@87838', 'kingjohn@87933', 'muchadoaboutnothing@95061', 'othello@99579', 'comedyoferrors@77712', 'juliuscaesar@104036', 'comedyoferrors@80878', 'comedyoferrors@64822', 'titusandronicus@101150', 'antonyandcleopatra@118525', 'cymbeline@75393', 'titusandronicus@120228', 'winterstale@95986', 'coriolanus@156382', 'kinghenryviii@38766', 'winterstale@68361', 'troilusandcre